<p style="font-family: Arial; font-size:2.75em;color:blue; font-style:bold"><br>
Projet 6 :<br><br>
Catégorisez automatiquement des questions<br><br>
</p><br>

* **Data Source / Data Source :** 
    - Data :
        - Outils d'extraction de data : https://data.stackexchange.com/stackoverflow
        - Script : https://github.com/EricJacquesPro/TextCategorization/blob/master/SQL/ExtractionDonnees.sql
    - Source Python : https://github.com/EricJacquesPro/TextCategorization
* **Description / Description : ** Projet 6 de la formation Data Scientist Proposée par OpenClassroom
    - Analyse
    - Entrainement
* **Auteur / Author : ** Eric JACQUES 
* **Date : ** 17/07/2020 

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
I - Sélection des datas entrantes</p>

Stack overfloaw met a disposition un outils en ligne permettant d'extraire le contenu de post diffusés sur le site internet.
(https://data.stackexchange.com/stackoverflow)<br>
En se basant sur la structure de la base de données(https://i.stack.imgur.com/JZHsN.png), il en ressort des données (tables) plus intéressantes que d'autres : Post, type de post, Tag, tags des posts <br>
Pour notre cas, tous les posts ne sont pas intéressants : Supprimé, score null, sans réponse, type de post....<br>
<br>
Parmis les posts, les données les plus explicites qui permettent de connaitre leurs sujets sont le body.<br>
<br>
Script téléchargeable sur https://github.com/EricJacquesPro/TextCategorization/blob/master/SQL/ExtractionDonnees.sql



<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
II - Data cleaning & preprocessing</p>

In [1]:
import sys
import os
import numpy as np
import pandas as pd
sys.path.insert(0, './Python/')

In [2]:
'''
python class for the data engineering (reading, cleaning, training...)
localised in ./Python
'''
from tagText import TagText 

C:\Users\naru_\Anaconda3\lib\site-packages\gensim\utils.py:865: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [3]:
cluster_number_min = 2
cluster_number_max = 10
cluster_number_step = 2

tagText = TagText()
print(tagText.urlDirectory)#folder for cvs file generated by SQL query (cf. I) 
print(tagText.fileName)#name of the cvs file generated by SQL query (cf. I)
tagText.nombre_post_entree = 50000
tagText.precision = 50000
data_question = tagText.read_source()
data_question.head()

Data/
QuestionVsTags.csv


Id                                               body  \
0  11227809  <p>Here is a piece of C++ code that shows some...   
1    927358  <p>I accidentally committed the wrong files to...   
2   2003505  <p>I want to delete a branch both locally and ...   
3    292357  <p>What are the differences between <code>git ...   
4    477816  <p>I've been messing around with <a href="http...   

                                               title  \
0  Why is processing a sorted array faster than p...   
1  How do I undo the most recent local commits in...   
2  How do I delete a Git branch locally and remot...   
3  What is the difference between 'git pull' and ...   
4             What is the correct JSON content type?   

                                                tags  \
0  <java><c++><performance><optimization><branch-...   
1  <git><version-control><git-commit><undo><pre-c...   
2  <git><version-control><git-branch><git-push><g...   
3        <git><version-control><git-pull><git-fetch>   
4                 <json><http-headers><content-type>   

                               SelectedTags      Name  
0        java,c++,performance,optimization,  Question  
1           git,version-control,git-commit,  Question  
2  git,version-control,git-branch,git-push,  Question  
3                      git,version-control,  Question  
4           json,http-headers,content-type,  Question

In [4]:
data_question.describe().T

count          mean           std  min         25%        50%  \
Id  50000.0  1.106364e+07  1.176372e+07  4.0  2219394.25  6609459.5   

            75%         max  
Id  16318680.25  61411498.0

In [5]:
print(tagText.stopwords)
'''Stop word issu to nltk.corpus'''

{'after', 'yours', 'and', 'for', 'mightn', 'is', 'up', "wouldn't", 'herself', 'has', 're', 'had', 'over', "doesn't", 'do', 'o', 'if', "you've", 'each', "didn't", 'an', 'with', 'nor', 'ma', 'hasn', "mightn't", 'been', 'her', 'about', "mustn't", 'hadn', 'doesn', 'too', 'now', 'further', "isn't", "you'll", 'below', 'once', 'more', 'during', 'yourselves', 'down', 'any', 'myself', 'no', 'll', 'was', "you're", "you'd", 'into', 'should', 'a', "hadn't", 'from', 'd', 'm', 'have', 'doing', 'does', 'this', 'above', 'theirs', "weren't", 'itself', 'those', 'because', 'who', 'hers', 'or', 'don', 'here', 'themselves', 'she', "don't", "wasn't", 's', 'all', 'shan', 'am', 'by', "hasn't", 'wasn', 'how', 'on', "should've", 'to', 'just', 'didn', 'before', "shan't", 'which', 'his', 'most', 'of', 'in', "it's", 'such', 'so', 'against', 'him', 'off', 'himself', 'their', 'are', 'haven', 'what', 'out', 'own', 'mustn', 'y', 'as', 'few', 've', 'again', 'i', 'than', 'it', 'same', 'these', 'its', 't', "aren't", 'the

'Stop word issu to nltk.corpus'

In [6]:
data_question['body'][1:9]

1    <p>I accidentally committed the wrong files to...
2    <p>I want to delete a branch both locally and ...
3    <p>What are the differences between <code>git ...
4    <p>I've been messing around with <a href="http...
5    <p>What is the use of the <code>yield</code> k...
6    <p>I mistakenly added files to Git using the c...
7    <p>After reading <a href="http://groups.google...
8    <p>I don't want to rename a remote branch, as ...
Name: body, dtype: object

<p style="font-family: Arial; color:red; font-style:bold">
Deleting nltk stopwords is not enough because there are lot of html and punctuation caracters
</p>

In [7]:
data_preprocessed = data_question['body'].apply(tagText.preprocessing)
print(data_preprocessed[1:9])

1    accidentally committed wrong files git pushed ...
2    want delete branch locally remotely failed att...
3                       differences git pull git fetch
4    ive messing around json time pushing text hurt...
5    use yield keyword python do example im trying ...
6    mistakenly added files git using command git a...
7    reading hidden features dark corners cstl comp...
8    want rename remote branch described rename mas...
Name: body, dtype: object


In [8]:
data_question.head()

Id                                               body  \
0  11227809  <p>Here is a piece of C++ code that shows some...   
1    927358  <p>I accidentally committed the wrong files to...   
2   2003505  <p>I want to delete a branch both locally and ...   
3    292357  <p>What are the differences between <code>git ...   
4    477816  <p>I've been messing around with <a href="http...   

                                               title  \
0  Why is processing a sorted array faster than p...   
1  How do I undo the most recent local commits in...   
2  How do I delete a Git branch locally and remot...   
3  What is the difference between 'git pull' and ...   
4             What is the correct JSON content type?   

                                                tags  \
0  <java><c++><performance><optimization><branch-...   
1  <git><version-control><git-commit><undo><pre-c...   
2  <git><version-control><git-branch><git-push><g...   
3        <git><version-control><git-pull><git-fetch>   
4                 <json><http-headers><content-type>   

                               SelectedTags      Name  
0        java,c++,performance,optimization,  Question  
1           git,version-control,git-commit,  Question  
2  git,version-control,git-branch,git-push,  Question  
3                      git,version-control,  Question  
4           json,http-headers,content-type,  Question

In [9]:
data_preprocessed.describe()

count                                                 50000
unique                                                50000
top       net 35 solution ended warning compiling msbuil...
freq                                                      1
Name: body, dtype: object

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III - Data - Bag of words</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.1 - Data - Bag of words - most frequent data</p>

In [10]:
import nltk
print(nltk.word_tokenize(data_preprocessed[0])[0:10])
print(nltk.tokenize.WhitespaceTokenizer().tokenize(data_preprocessed[0])[0:10])
# Tokenize using Punctuations
print(nltk.tokenize.WordPunctTokenizer().tokenize(data_preprocessed[0])[0:10])
print(nltk.tokenize.TreebankWordTokenizer().tokenize(data_preprocessed[0])[0:10])

['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']
['piece', 'c', 'code', 'shows', 'peculiar', 'behavior', 'strange', 'reason', 'sorting', 'data']


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.2 - Data - Bag of words - Nb of occurence</p>

In [11]:
import nltk
from collections import defaultdict
    
corpora = defaultdict(list)
        
tokenizer = nltk.RegexpTokenizer(r'\w+')
for id, row in data_preprocessed.iteritems():
    for word in tokenizer.tokenize(row):
        if not word in corpora :
            corpora[word] = 0
        #print(word)
        corpora[word] += 1

In [12]:
import matplotlib.pyplot as plt
minimum_count = 2#200
def count_word_occurencies(df):
        corpora = defaultdict(list)                
        tokenizer = nltk.RegexpTokenizer(r'\w+')
        for id, row in df.iteritems():
            for word in tokenizer.tokenize(row):
                if not word in corpora :
                    corpora[word] = 0
                #print(word)
                corpora[word] += 1
        corpora = dict((k, v) for k, v in corpora.items() if ((v > minimum_count)))
        sorted(corpora)
        print('''test0''')
        print(corpora)
        corpora = dict((k, v) for k, v in corpora.items() if ((v > 1)))
        print('''test''')
        print(corpora)
        return (sorted(corpora.items(), reverse=True,  key=lambda x: x[1]))

In [13]:
dico = count_word_occurencies(data_preprocessed)

test0
{'mmeaning': 3, 'larger': 233, 'scrollbar': 89, 'joinx': 3, 'snbuffer': 3, 'mention': 290, 'delegatecommand': 3, 'dtargety': 3, 'unnecessarily': 16, 'elementum': 4, 'thirdly': 3, 'androidpaddingtop5px': 8, '180009402': 12, 'functionmsg': 9, '222px': 3, 'pagebreakbefore': 3, '4f4e': 4, 'reporter': 5, 'descriptorrefs': 6, 'native': 544, 'constantly': 76, '1578': 3, 'thispluginid': 3, 'car1': 3, 'clangllvm': 3, 'dp': 34, 'ondata': 4, 'keysd1': 4, 'flow': 199, 'elt1': 5, 'primitivesum': 3, 'zepto': 4, 'fstream': 20, 'ec': 5, 'hybrid': 10, 'overcomplicating': 3, 'storagetype': 3, 'phantomexit': 3, '0010615711': 6, 'viewmeasurespecatmost': 4, 'm2': 27, 'argumentsi': 3, 'anyones': 4, 'ror': 36, 'arrayadapterstring': 12, 'bezier': 4, 'assemblyinfocs': 16, 'sequelize': 11, 'androiddividerheight0dp': 3, 'pushmsg': 3, 'cent': 5, 'mycat': 3, 'woes': 4, 'itoa': 10, 'alertdanger': 4, 'outofthebox': 16, 'servicepoint': 5, 'requestcontenttype': 5, 'preinstalled': 5, 'command2': 10, 'trtdcolumn1t

In [14]:
print(len(dico))
dico

43111


[('like', 19990),
 ('using', 18034),
 ('im', 17220),
 ('use', 16208),
 ('code', 14970),
 ('want', 14812),
 ('get', 14370),
 ('way', 14046),
 ('file', 13377),
 ('would', 13362),
 ('new', 12571),
 ('error', 11432),
 ('this', 11194),
 ('1', 11100),
 ('one', 10935),
 ('string', 10805),
 ('class', 10313),
 ('public', 9597),
 ('return', 9568),
 ('function', 9542),
 ('know', 8541),
 ('need', 8479),
 ('0', 7968),
 ('following', 7851),
 ('ive', 7650),
 ('2', 7618),
 ('something', 7587),
 ('example', 7572),
 ('it', 7301),
 ('set', 7285),
 ('data', 7196),
 ('work', 6942),
 ('c', 6899),
 ('id', 6897),
 ('method', 6789),
 ('var', 6685),
 ('value', 6648),
 ('name', 6381),
 ('find', 6203),
 ('trying', 6159),
 ('div', 6085),
 ('also', 6003),
 ('object', 5870),
 ('int', 5804),
 ('tried', 5716),
 ('could', 5688),
 ('git', 5644),
 ('line', 5634),
 ('type', 5500),
 ('question', 5467),
 ('files', 5440),
 ('time', 5394),
 ('run', 5376),
 ('make', 5260),
 ('see', 5172),
 ('list', 5133),
 ('problem', 5102),
 

In [15]:
print(tagText.count_word_occurencies(data_preprocessed))

[('like', 19990), ('using', 18034), ('im', 17220), ('use', 16208), ('code', 14970), ('want', 14812), ('get', 14370), ('way', 14046), ('file', 13377), ('would', 13362), ('new', 12571), ('error', 11432), ('this', 11194), ('1', 11100), ('one', 10935), ('string', 10805), ('class', 10313), ('public', 9597), ('return', 9568), ('function', 9542), ('know', 8541), ('need', 8479), ('0', 7968), ('following', 7851), ('ive', 7650), ('2', 7618), ('something', 7587), ('example', 7572), ('it', 7301), ('set', 7285), ('data', 7196), ('work', 6942), ('c', 6899), ('id', 6897), ('method', 6789), ('var', 6685), ('value', 6648), ('name', 6381), ('find', 6203), ('trying', 6159), ('div', 6085), ('also', 6003), ('object', 5870), ('int', 5804), ('tried', 5716), ('could', 5688), ('git', 5644), ('line', 5634), ('type', 5500), ('question', 5467), ('files', 5440), ('time', 5394), ('run', 5376), ('make', 5260), ('see', 5172), ('list', 5133), ('problem', 5102), ('user', 5003), ('two', 4889), ('project', 4888), ('3', 4

<p style="font-family: Arial; color:red; font-style:bold">
Generating a dictionary of the most frequent terms is not interesting because we find a lot of words without great interest
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
III.2 - Data - Bag of words - TF-IDF</p>

In [16]:
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import TfidfVectorizer

stemmer = nltk.stem.porter.PorterStemmer()
stopword = nltk.corpus.stopwords.words('english')

#X = data_preprocessed.unique()
X = data_preprocessed[0:9].unique()

def stem_and_filter(doc):
    tokens = [stemmer.stem(w) for w in analyzer(doc)]
    return [token for token in tokens if token.isalpha()]

analyzer = TfidfVectorizer().build_analyzer()
cv = TfidfVectorizer(lowercase=True, stop_words="english", analyzer=stem_and_filter, min_df=0.00, max_df=0.3)  # we remove words if it appears in more than 30 % of the corpus (not found stopwords like Box, Christmas and so on)
word_count_vector = cv.fit_transform(X)
print("TF_IDF_matrix :", word_count_vector.shape, "of", word_count_vector.dtype)
tfidf_transformer=TfidfTransformer(smooth_idf=True,use_idf=True)
tfidf_transformer.fit(word_count_vector)
# print idf values
df_idf = pd.DataFrame(tfidf_transformer.idf_, index=cv.get_feature_names(),columns=["tf_idf_weights"])
 
# sort ascending
df_idf.sort_values(by=['tf_idf_weights'])


TF_IDF_matrix : (9, 247) of float64


tf_idf_weights
file                              2.203973
time                              2.203973
int                               2.203973
branch                            2.203973
start                             2.203973
thi                               2.203973
return                            2.203973
tri                               2.203973
piec                              2.203973
repositori                        2.203973
id                                2.203973
pull                              2.203973
remot                             2.203973
commit                            2.203973
compil                            2.203973
result                            2.203973
standard                          2.203973
differ                            2.203973
undo                              2.203973
similar                           2.203973
yet                               2.203973
well                              2.203973
want                              2.203973
new                               2.203973
complet                           2.203973
main                              2.203973
run                               2.203973
use                               2.203973
selfmedian                        2.609438
read                              2.609438
...                                    ...
iostream                          2.609438
initi                             2.609438
exampl                            2.609438
extrem                            2.609438
fail                              2.609438
faster                            2.609438
featur                            2.609438
fetch                             2.609438
first                             2.609438
follow                            2.609438
found                             2.609438
from                              2.609438
gather                            2.609438
gcc                               2.609438
intarrays                         2.609438
gener                             2.609438
getchildcandidatesself            2.609438
githubcomgitusergitproject        2.609438
go                                2.609438
goe                               2.609438
great                             2.609438
happen                            2.609438
here                              2.609438
hidden                            2.609438
hurt                              2.609438
im                                2.609438
import                            2.609438
independ                          2.609438
getchildcandid                    2.609438
yield                             2.609438

[247 rows x 1 columns]

<p style="font-family: Arial; color:red; font-style:bold">
The words proposed following the TF-IDF generation seem more interesting than the list of the most frequent words.
We will favor TF-IDF for the rest.
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV - Data - Tag genetaor </p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.1 - Data - Tag generator - Unsupervised - By nb of occurence</p>

In [17]:
dict_tag = count_word_occurencies(data_preprocessed)
dict_tag = str(dict_tag)
dict_tag


test0
{'mmeaning': 3, 'larger': 233, 'scrollbar': 89, 'joinx': 3, 'snbuffer': 3, 'mention': 290, 'delegatecommand': 3, 'dtargety': 3, 'unnecessarily': 16, 'elementum': 4, 'thirdly': 3, 'androidpaddingtop5px': 8, '180009402': 12, 'functionmsg': 9, '222px': 3, 'pagebreakbefore': 3, '4f4e': 4, 'reporter': 5, 'descriptorrefs': 6, 'native': 544, 'constantly': 76, '1578': 3, 'thispluginid': 3, 'car1': 3, 'clangllvm': 3, 'dp': 34, 'ondata': 4, 'keysd1': 4, 'flow': 199, 'elt1': 5, 'primitivesum': 3, 'zepto': 4, 'fstream': 20, 'ec': 5, 'hybrid': 10, 'overcomplicating': 3, 'storagetype': 3, 'phantomexit': 3, '0010615711': 6, 'viewmeasurespecatmost': 4, 'm2': 27, 'argumentsi': 3, 'anyones': 4, 'ror': 36, 'arrayadapterstring': 12, 'bezier': 4, 'assemblyinfocs': 16, 'sequelize': 11, 'androiddividerheight0dp': 3, 'pushmsg': 3, 'cent': 5, 'mycat': 3, 'woes': 4, 'itoa': 10, 'alertdanger': 4, 'outofthebox': 16, 'servicepoint': 5, 'requestcontenttype': 5, 'preinstalled': 5, 'command2': 10, 'trtdcolumn1t

"[('like', 19990), ('using', 18034), ('im', 17220), ('use', 16208), ('code', 14970), ('want', 14812), ('get', 14370), ('way', 14046), ('file', 13377), ('would', 13362), ('new', 12571), ('error', 11432), ('this', 11194), ('1', 11100), ('one', 10935), ('string', 10805), ('class', 10313), ('public', 9597), ('return', 9568), ('function', 9542), ('know', 8541), ('need', 8479), ('0', 7968), ('following', 7851), ('ive', 7650), ('2', 7618), ('something', 7587), ('example', 7572), ('it', 7301), ('set', 7285), ('data', 7196), ('work', 6942), ('c', 6899), ('id', 6897), ('method', 6789), ('var', 6685), ('value', 6648), ('name', 6381), ('find', 6203), ('trying', 6159), ('div', 6085), ('also', 6003), ('object', 5870), ('int', 5804), ('tried', 5716), ('could', 5688), ('git', 5644), ('line', 5634), ('type', 5500), ('question', 5467), ('files', 5440), ('time', 5394), ('run', 5376), ('make', 5260), ('see', 5172), ('list', 5133), ('problem', 5102), ('user', 5003), ('two', 4889), ('project', 4888), ('3', 

In [18]:
def unsupervised_tag(dict_word_key, new_question, number_max_tag):
    tags = [word for word in new_question.split() if (word in dict_word_key)]
    return tags[0:number_max_tag]

print(unsupervised_tag(dict_tag, "How save my code source with soft like git", 20))
print(unsupervised_tag(dict_tag, "How save my code source with soft like like git", 2))
#for word in "like git branche totot, test".split() if (word in dict_word_key)

['save', 'my', 'code', 'source', 'with', 'soft', 'like', 'git']
['save', 'my']


In [19]:
tagText.unsupervised_tag(dict_tag, "How save my code source with soft like git", 2)

['save', 'my']

<p style="font-family: Arial; color:red; font-style:bold">
Not interesting because we receive words without interest
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.2-a - Data - Tag generator - Unsupervised - LDA</p>

<p style="font-family: Arial; color:red; font-style:bold">
For more detals about LDA and to generate lda.joblib, please, see the notebook Projet_V2_LDA-v2-Detals.ipynb
</p>

In [20]:
'''
If you want to load lda model generated in the other notebook
'''
from joblib import dump, load
lda_load = load('lda.joblib') 
df_topic_keywords_load = load('df_lda_topic_keywords.joblib') 
tf_vectorizer_load = load('tf_lda_vectorizer.joblib')

print(lda_load)

LatentDirichletAllocation(batch_size=128, doc_topic_prior=None,
             evaluate_every=-1, learning_decay=0.7,
             learning_method='online', learning_offset=10.0,
             max_doc_update_iter=100, max_iter=10, mean_change_tol=0.001,
             n_components=10, n_jobs=-1, n_topics=32, perp_tol=0.1,
             random_state=100, topic_word_prior=None,
             total_samples=1000000.0, verbose=0)


In [21]:
'''
If you want to generate lda model
'''
lda_load, df_topic_keywords_load, tf_vectorizer_load = tagText.lda_prepare_tag(data_preprocessed, 32)


C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}
Log Likelihood:  -18997621.8565
Perplexity:  8009.42791632
{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}


In [22]:

print('Topics From working class : ')
tagText.display_topics(lda_load, tf_vectorizer_load.get_feature_names(), 10)


Topics From working class : 
Topic : 0 :
server request foo bar post error app client http password
Topic : 1 :
set application html app script path controller using site load
Topic : 2 :
input jquery multiple lines event action checked selected box modified
Topic : 3 :
new object objects create properties creating add instance feature break
Topic : 4 :
numpy ex register num 255 ipython volume notebook tmp non
Topic : 5 :
import component template match expression export tools contain angular word
Topic : 6 :
thanks process rails os open port running mac windows happen
Topic : 7 :
table select database data query id sql column mysql null
Topic : 8 :
file files run directory command using want im folder build
Topic : 9 :
test date item string var format state index names loop
Topic : 10 :
view button click left screen text window characters layout right
Topic : 11 :
list value key values field fields keys order dictionary lists
Topic : 12 :
web model url framework aspnet length mvc desi

In [23]:
print(tagText.lda_predict( "How to cast number as integer in java", lda_load, df_topic_keywords_load, tf_vectorizer_load, 5))

int 10 number long compiler


<p style="font-family: Arial; color:red; font-style:bold">
LDA prediction seems to be interesting
</p>

<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.2-b - Data - Tag generator - Unsupervised - MNF</p>

In [24]:
nmf_tagText, df_nmf_topic_keywords, tf_mnf_vectorizer = tagText.nmf_prepare_tag(data_preprocessed, 32)
            
tagText.nmf_predict('git est un outils de code source.', nmf_tagText, df_nmf_topic_keywords, tf_mnf_vectorizer, 5)

original reconstruction error automatically calculated -> TRAIN:  214.304483129
Manually calculated rec-error train:  214.304460759


'git commit repository push changes'

<p style="font-family: Arial; color:red; font-style:bold">
NMF prediction seems to be interesting
</p>

In [25]:
from joblib import dump, load
dump(nmf_tagText, 'nmf.joblib') 
dump(df_nmf_topic_keywords, 'df_nmf_topic_keywords.joblib') 
dump(tf_mnf_vectorizer, 'tf_mnf_vectorizer.joblib') 

nmfLoad = load('nmf.joblib') 
print(nmfLoad)

NMF(alpha=0.1, beta_loss='frobenius', init='nndsvd', l1_ratio=0.5,
  max_iter=200, n_components=32, random_state=1, shuffle=False,
  solver='cd', tol=0.0001, verbose=0)


In [26]:
lda_tagText, df_lda_topic_keywords, tf_lda_vectorizer = tagText.lda_prepare_tag_and_save(data_preprocessed)
mnf_tagText, df_nmf_topic_keywords, tf_mnf_vectorizer = tagText.nmf_prepare_tag_and_save(data_preprocessed)

print(tagText.lda_predict('git est un outils de code source. C\'est bien', lda_tagText, df_lda_topic_keywords, tf_lda_vectorizer, 5))
print(tagText.nmf_predict('git est un outils de code source. C\'est bien', mnf_tagText, df_nmf_topic_keywords, tf_mnf_vectorizer, 5))


C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}
Log Likelihood:  -18997621.8565
Perplexity:  8009.42791632
{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}
original reconstruction error automatically calculated -> TRAIN:  214.304483129
Manually calculated rec-error train:  214.304460759
code java exception run error
git commit repository push changes


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
IV.3 - Data - Tag generator - Supervised</p>

In [27]:
classifier, tags = tagText.supervised_prepare_tag(data_preprocessed, data_question['SelectedTags'])
message = 'git est un outils de code source. C\'est bien'

print(message)

print(tagText.supervised_predict(message, classifier, tags))

git est un outils de code source. C'est bien
['android', 'c#', 'git', 'java', 'javascript', 'python']


In [28]:
print(tagText.supervised_predict(data_preprocessed[0], classifier, tags ))

['android', 'c#', 'c++', 'java', 'javascript', 'python']


<p style="font-family: Arial; font-size:1.75em;color:#2462C0; font-style:bold"><br>
V - Resultat</p>

In [29]:

import numpy as np
import nltk
import pandas as pd
import os
import sys

sys.path.insert(0, './Python/')

from tagText import TagText


tagText = TagText()
print(tagText.urlDirectory)
print(tagText.fileName)
nombre_post_entree = 50000
precision = 50000
tagText.nombre_post_entree = nombre_post_entree
tagText.precision = precision
nombre_suggestion = 6

def supervisedTagPurposer():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'false', 'false')

def supervisedTagPurposerAndReload():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'true', 'false')

def supervisedTagPurposerAndReloadAndSave():
    return tagPurposer('supervised', 'This is a test to have tag GIT & branche', 'true', 'true')

def tagLDAPurposer():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'false', 'false')

def tagLDAPurposerAndReload():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'true', 'false')

def tagLDAPurposerAndReloadAndSave():
    return tagPurposer('LDA', 'This is a test to have tag GIT & branche', 'true', 'true')

def tagNMFPurposer():
    return tagPurposer('NMF', 'This is a test to have tag GIT & branche', 'false', 'false')

def tagNMFPurposerAndReload():
    return tagPurposer('NMF', 'This is a test to have tag GIT & branche', 'true', 'false')

def tagNMFPurposerAndReloadAndSave():
    return tagPurposer('NMF', 'This is a test to have tag GIT & branche', 'true', 'true')

def tagPurposer(mode, message, reload, saveModel):
    if mode.lower() == 'supervised':
        return superviedTagPurposerFromMessage(message, reload.lower(), saveModel.lower())
    if mode.lower() == 'lda' or mode.lower() =='nmf':
        return unsuperviedTagTFIDFPurposerFromMessage(mode.lower(), message, reload.lower(), saveModel.lower())
    return '/i\\Mode indefined/i\\'

def superviedTagPurposerFromMessage(message, reload, saveModel):
    tagText = TagText()
    tagText.nombre_post_entree = nombre_post_entree
    tagText.precision = precision
    tags = ''
    if reload.lower() == 'true':
        data_question = tagText.read_source()
        data_preprocessed = data_question['body'].apply(tagText.preprocessing)
        if saveModel.lower() == 'true':
            classifier, tags_existants = tagText.supervised_prepare_tag_and_save(data_preprocessed, data_question['SelectedTags'])
            tags = tagText.supervised_predict(message, classifier, tags_existants)
        else :
            classifier, tags_existants = tagText.supervised_prepare_tag(data_preprocessed, data_question['SelectedTags'])
            tags = tagText.supervised_predict(message, classifier, tags_existants)
    else:
        classifier, tags_existants = tagText.supervised_prepare_tag_load()
        tags = tagText.supervised_predict(message, classifier, tags_existants)
    return tags

def unsuperviedTagTFIDFPurposerFromMessage(option, message, reloadModel, saveModel):
    tagText = TagText()
    tagText.nombre_post_entree = nombre_post_entree
    tagText.precision = precision
    tags = ''
    if option.lower() != 'lda' and option.lower() != 'nmf':
        return '/i\\Mode indefined/i\\'
    if reloadModel.lower() == 'true':
        data_question = tagText.read_source()
        data_preprocessed = data_question['body'].apply(tagText.preprocessing)
        if option.lower() == 'lda':
            if saveModel.lower() == 'true':
                lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.lda_prepare_tag_and_save(data_preprocessed)
                tags = tagText.lda_predict(message, lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
            else:
                lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.lda_prepare_tag(data_preprocessed)
                tags = tagText.lda_predict(message, lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
        if option.lower() == 'nmf':
            if saveModel.lower() == 'true':
                nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.nmf_prepare_tag_and_save(data_preprocessed)
                tags = tagText.nmf_predict(message, nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
            else:
                nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.nmf_prepare_tag(data_preprocessed)
                tags = tagText.nmf_predict(message, nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
    else:
        if option.lower() == 'lda':
            lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.lda_prepare_tag_load()
            tags = tagText.lda_predict(message, lda_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
        if option.lower() == 'nmf':
            nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText = tagText.nmf_prepare_tag_load()
            tags = tagText.nmf_predict(message, nmf_tagText, df_topic_keywords_tagText, tf_vectorizer_tagText, nombre_suggestion)
    return tags


Data/
QuestionVsTags.csv


In [30]:
tagLDAPurposerAndReloadAndSave()

C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}
Log Likelihood:  -18997621.8565
Perplexity:  8009.42791632
{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}


'git branch repository changes remote master'

In [31]:
supervisedTagPurposerAndReload()

"['android', 'c#', 'java', 'javascript', 'python']"

In [32]:
supervisedTagPurposerAndReloadAndSave()

"['android', 'c#', 'java', 'javascript', 'python']"

In [33]:
supervisedTagPurposer()

"['android', 'c#', 'java', 'javascript', 'python']"

In [34]:
tagLDAPurposerAndReload()

C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}
Log Likelihood:  -18997621.8565
Perplexity:  8009.42791632
{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}


'git branch repository changes remote master'

In [35]:
tagLDAPurposerAndReloadAndSave()

C:\Users\naru_\Anaconda3\lib\site-packages\sklearn\decomposition\online_lda.py:294: DeprecationWarning: n_topics has been renamed to n_components in version 0.19 and will be removed in 0.21
  DeprecationWarning)


{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}
Log Likelihood:  -18997621.8565
Perplexity:  8009.42791632
{'n_topics': 32, 'doc_topic_prior': None, 'learning_offset': 10.0, 'batch_size': 128, 'total_samples': 1000000.0, 'evaluate_every': -1, 'topic_word_prior': None, 'max_doc_update_iter': 100, 'perp_tol': 0.1, 'n_jobs': -1, 'mean_change_tol': 0.001, 'n_components': 10, 'verbose': 0, 'learning_decay': 0.7, 'learning_method': 'online', 'random_state': 100, 'max_iter': 10}


'git branch repository changes remote master'

In [36]:
tagLDAPurposer()

'git branch repository changes remote master'

In [37]:
tagNMFPurposerAndReload()

original reconstruction error automatically calculated -> TRAIN:  214.304483129
Manually calculated rec-error train:  214.304460759


'git commit repository push changes repo'

In [38]:
tagNMFPurposerAndReloadAndSave()

original reconstruction error automatically calculated -> TRAIN:  214.304483129
Manually calculated rec-error train:  214.304460759


'git commit repository push changes repo'

In [39]:
tagNMFPurposer()

'git commit repository push changes repo'

Une API :  https://ejacques.pythonanywhere.com/apiTagGenerator/

Un depot GIT : https://github.com/EricJacquesPro/TextCategorization/